In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [4]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO      MARCA       Date  \
2409  C202515   2025-10-13 2025-11-02       21  BOTICARIO 2025-10-13   

      NUM_CICLO ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
2409         15     C2025    C202518               59      1

In [5]:
ciclo_lanc = filtered_calendario['Ciclo'].max()

In [6]:
ciclo_lanc

'C202515'

In [7]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C15\arquivos para geração da sugestão\SIMILARES\PRODUTOS SIMILARES - BOT.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO', 'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [8]:
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('str')

df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].replace(r'\.0$', '', regex=True)




In [9]:


df_similares = df_similares[df_similares['PRODUTO SIMILAR']!= 'nan']

df_similares['PRODUTO SIMILAR'].value_counts()

PRODUTO SIMILAR
52004    1
52008    1
52005    1
72929    1
53389    1
57474    1
52012    1
58138    1
49973    1
1006     1
53342    1
47963    1
84056    1
25458    1
48136    1
51448    1
1004     1
58373    1
75792    1
55659    1
48635    1
48621    1
59306    1
49225    1
49228    1
57759    1
55766    1
87000    1
87771    1
Name: count, dtype: int64

In [10]:
df_similares.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH'],
      dtype='object')

In [11]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C14\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - BOT - 202514.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [12]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv[~df_pdv['PDV'].isin(['910173', '910291'])]

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv_origi = df_pdv_origi[~df_pdv_origi['PDV'].isin(['910173', '910291'])]

In [13]:
df_pdv[df_pdv['PDV']==24293]

PDV CANAL                     DESCRIÇÃO PDV DESC REGIÃO ESTADO CIDADE  \
82  24293   HIB  COMERCIO-HIB MORRO DO CHAPEU      NaN    NaN    NaN    NaN   

     UF        MARCA  ANALISTA   GESTÃO                  SUPERVISOR STATUS  
82  BA3  O BOTICARIO  MARCYARA  Alysson  Arianne Sodré [Provisório]  ATIVO

In [14]:


df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

df_pdv = df_pdv[df_pdv['STATUS'] != "INATIVO"]

df_pdv = df_pdv[df_pdv['STATUS'] != "MATRIZ"]

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != 'Inativa']

df_pdv['MATCH'] = 1

In [15]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [16]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\Bot - C13\LANÇAMENTOS\arquivos para geração da sugestão\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


(141690, 47)

In [17]:
df_draft = df_draft.drop(columns=['Categoria'])

In [18]:
df_draft.columns[7:25]

Index(['Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [19]:
df_draft[df_draft['PDV']==24293]

PDV Classe    SKU                                 Descrição  \
12      24293      C  49014        ACCORDES CREM DES HID CPO 200ml V2   
90      24293      C  49016             ACCORDES DES BDY SPR 100ml V6   
168     24293      B  48141                  ACCORDES DES COL 80ml V5   
246     24293      B  51213         ACCORDES DES COL HARMONIA 80ml V4   
324     24293      E  86017              ARBO CREM PRE/POS BARBA 100g   
...       ...    ...    ...                                       ...   
141535  24293      E  50571     QDB SRUM FAC LEVANTA TUDO SKIN Q 30ml   
141567  24293      E  50574      QDB SRUM FAC PREENCHE TUDO SKIN 30ml   
141599  24293      E   9403        QDB SRUM FAC TRIP COMB SKIN Q 30ml   
141629  24293      E  50568  QDB SRUM REST FAC ACORD/GLOW SKIN Q 30ml   
141661  24293      E  53912                      QDB TOALHA DEMAQ ALG   

                     Subcategoria Lançamento Desativação  \
12           CUIDADOS COM O CORPO        NaN         NaN   
90           DESODORANTE FEMININO        NaN         NaN   
168           PERFUMARIA FEMININA        NaN         NaN   
246           PERFUMARIA FEMININA        NaN         NaN   
324                   PRÉ-BARBEAR        C08         NaN   
...                           ...        ...         ...   
141535  HIDRATANTES E TRATAMENTOS        NaN         NaN   
141567  HIDRATANTES E TRATAMENTOS        NaN         NaN   
141599  HIDRATANTES E TRATAMENTOS        NaN         NaN   
141629  HIDRATANTES E TRATAMENTOS        NaN         NaN   
141661       FUNCIONAIS MAQUIAGEM        NaN         NaN   

        Histórico de Vendas do Ciclo 202410  \
12                                        0   
90                                        0   
168                                       0   
246                                       0   
324                                       0   
...                                     ...   
141535                                    0   
141567                                    0   
141599                                    0   
141629                                    0   
141661                                    0   

        Histórico de Vendas do Ciclo 202411  \
12                                        0   
90                                        0   
168                                       0   
246                                       0   
324                                       0   
...                                     ...   
141535                                    0   
141567                                    0   
141599                                    0   
141629                                    0   
141661                                    0   

        Histórico de Vendas do Ciclo 202412  ...  Item Desativado  \
12                                        0  ...              Não   
90                                        0  ...              Não   
168                                       0  ...              Não   
246                                       0  ...              Não   
324                                       0  ...              Não   
...                                     ...  ...              ...   
141535                                    0  ...              Não   
141567                                    0  ...              Não   
141599                                    0  ...              Não   
141629                                    0  ...              Não   
141661                                    0  ...              Não   

        Data Prevista Regularização  Carteira Bloqueada Para Novos Pedidos  \
12                                0                                    Não   
90                                0                                    Não   
168                               0                                    Não   
246               Baixo Atendimento                                    Não   
324                               0                            

In [20]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[7:25]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_101180\1463083786.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [21]:
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('Int64')
df_similares['PRODUTO SIMILAR'].head()

0    52004
1    52004
2    52004
3    52004
4    52004
Name: PRODUTO SIMILAR, dtype: Int64

In [22]:
df_similares['PDV'] = df_similares['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [23]:
df_final

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
...                  ...                                                ...   
2286               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2287               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2288               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2289               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2290               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   

      PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
1               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
2               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
3               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
4               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
...               ...                                       ...           ...   
2286            87771                                         0             0   
2287            87771                                         0             0   
2288            87771                                         0             0   
2289            87771                                         0             0   
2290            87771                                         0             0   

     FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ...  \
0     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
1     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
2     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
3     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
4     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
...   ...  ...                  ...         ...            ...  ...   
2286  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...   
2287  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...   
2288  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...   
2289  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...   
2290  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...   

     Data Prevista Regularização Carteira Bloqueada Para Novos Pedidos  \
0                              0                                   Não   
1                              0                                   Não   
2                              0                                   Não   
3                              0                                   Não   
4                              0                                   Não   
...                          ...                                   ...   
2286                         NaN                                   NaN   
2287                         NaN                                   NaN   
2288                         NaN                                   NaN   
2289                         NaN                                   NaN   
2290                         NaN                                   NaN   

     Planograma Quantidade por caixa  Preço Sell In  Quantidade  \
0           3.0                 30.0          23.62         0.0   
1           3.0                 30.0          23.62         9.0   
2           3.0                 30.0          23.62         4.0   
3           0.0                 30.0          23.62         0.0   
4      

In [24]:
df_similares= df_similares[df_similares['PRODUTO SIMILAR'].notna()]

df_similares['PRODUTO SIMILAR'].value_counts()

PRODUTO SIMILAR
52004    79
52008    79
52005    79
72929    79
53389    79
57474    79
52012    79
58138    79
49973    79
1006     79
53342    79
47963    79
84056    79
25458    79
48136    79
51448    79
1004     79
58373    79
75792    79
55659    79
48635    79
48621    79
59306    79
49225    79
49228    79
57759    79
55766    79
87000    79
87771    79
Name: count, dtype: Int64

In [25]:
df_final['SKU'].value_counts()

SKU
52004.0    77
52008.0    77
52005.0    77
53389.0    77
52012.0    77
58138.0    77
49973.0    77
47963.0    77
84056.0    77
25458.0    77
48136.0    77
51448.0    77
1004.0     77
75792.0    77
55659.0    77
48635.0    77
48621.0    77
59306.0    77
57759.0    77
55766.0    77
Name: count, dtype: int64

In [26]:
#df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\VENDAS_DIARIAS\FormFiltroConsultaVendaSintetica_17_06_2025_14_04_40.xls")
#df_venda_diaria.shape

In [27]:
df_venda_diaria = pd.read_csv(
    r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C15\arquivos para geração da sugestão\VENDAS_DIARIAS\vendas 20250815.csv",
    sep=';',
    dtype={'SKU_2': str},decimal=',')

In [28]:
df_venda_diaria['VENDAS_CICLO'] = df_venda_diaria['VENDAS_CICLO'].str.replace(r'\.', '', regex=True)

In [29]:
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO VENDAS_CICLO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [30]:
#df_venda_diaria['Ciclo'] = df_venda_diaria['Ciclo'].str.replace("C","C20") 

df_venda_diaria = df_venda_diaria.rename(columns={'VENDAS_CICLO':'Vendas_Total'})

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [31]:
df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].str.replace(',', '.', regex=False)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype('float')

df_venda_diaria['Vendas_Total'] = round(df_venda_diaria['Vendas_Total'],0)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype(str)

df_venda_diaria['Vendas_Total'] = (
    df_venda_diaria['Vendas_Total']
    .str.replace('.0', '', regex=False)
    .str.replace('.', '', regex=False)
    .astype('Int64')
)


df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [32]:
df_venda_diaria2 = df_venda_diaria.pivot_table(
    index=["PDV", "SKU", "DESCRICAO"],
    columns="Ciclo",
    values="Vendas_Total",
    fill_value=0
).reset_index()

# Se quiser, reorganize as colunas colocando os ciclos ao final
df_venda_diaria.columns.name = None

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [33]:
df_venda_diaria.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'Vendas_Total', 'Ciclo'], dtype='object')

In [34]:
df_venda_diaria

PDV     SKU                                 DESCRICAO  \
0        12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1        20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2        20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3         5699  47.950                          ZAAD EDP 95ml V6   
4        20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   
...        ...     ...                                       ...   
1663315  20996  83.039                 QUASAR DES COL RUSH 100ml   
1663316  20970  52.025           BOTI BABY SAB LIQ GLIC V2 400ml   
1663317  20996  93.069  LA PIEL D/COL SPR CP PER AMBR DOUR 200ml   
1663318  13427  51.279         MAKE B BAS LIQ C/ GLYC TX 140 30g   
1663319  21278  52.014    CJ FLAC OUI EDP ICONIQUE INTENSE 3x1ml   

         Vendas_Total    Ciclo  
0                  11  C202307  
1                   1  C202405  
2                   5  C202409  
3                  12  C202406  
4                   2  C202416  
...               ...      ...  
1663315             1  C202415  
1663316             6  C202511  
1663317            10  C202414  
1663318             1  C202309  
1663319             2  C202511  

[1663320 rows x 5 columns]

In [35]:
#df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

#df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

#df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

#df_venda_diaria = df_venda_diaria.drop(columns='Date')

#df_venda_diaria.shape

In [36]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
#df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
#df_venda_diaria['Quantidade Acumulada'] = (df_venda_diaria.groupby(['Unidade de Negócio', 'Código do Produto'])['Quantidade'].cumsum())  # acumulado por grupo até a data da linha

#df_venda_diaria.shape

In [37]:
#df_venda_diaria = df_venda_diaria.drop_duplicates()

#df_venda_agrupado = df_venda_diaria.fillna(0).groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
#df_venda_agrupado

In [38]:
#df_venda_agrupado[(df_venda_agrupado['Ciclo']=='C202213')&(df_venda_agrupado['Código do Produto']==81054)&(df_venda_agrupado['PDV']=='20994')]

In [39]:
#df_venda_agrupado[['Ciclo','Código do Produto','PDV']].dtypes

In [40]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].dtypes

CICLO SIMILAR      object
PRODUTO SIMILAR     Int64
PDV                 Int64
dtype: object

In [41]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(2291, 75)

In [42]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [43]:
df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
1            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
2            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
3            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
4            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   

  FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ...  \
0  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
1  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
2  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
3  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   
4  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...   

  Item analisado Histórico de Vendas do Ciclo 202409 match_x CRESCIMENTO  \
0            Não                                 NaN     1.0     -0.0154   
1            Não                                 NaN     1.0     -0.0341   
2            Não                                 NaN     1.0     -0.0138   
3            Não                                 NaN     1.0     -0.0595   
4            Não                                 NaN     1.0     -0.0171   

     Ciclo  INICIO CICLO  FIM CICLO DURAÇÃO match_y dias_ate_inicio  
0  C202515    2025-10-13 2025-11-02      21       1              59  
1  C202515    2025-10-13 2025-11-02      21       1              59  
2  C202515    2025-10-13 2025-11-02      21       1              59  
3  C202515    2025-10-13 2025-11-02      21       1              59  
4  C202515    2025-10-13 2025-11-02      21       1              59  

[5 rows x 75 columns]

In [44]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [45]:

df_venda_diaria = df_venda_diaria.rename(columns={'Vendas_Total':'Vendas Ciclo Lançamento'})
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47.950                          ZAAD EDP 95ml V6   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [46]:
df_final['CICLO SIMILAR'] = df_final['CICLO SIMILAR'].fillna('0')
df_final['CICLO SIMILAR'] 

0        C202315
14       C202315
28       C202315
42       C202315
56       C202315
          ...   
19192          0
19193          0
19194          0
19195          0
19196          0
Name: CICLO SIMILAR, Length: 2291, dtype: object

In [47]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].head()

CICLO SIMILAR  PRODUTO SIMILAR    PDV
0        C202315            52004  12522
14       C202315            52004  12817
28       C202315            52004  12818
42       C202315            52004  12820
56       C202315            52004  12823

In [48]:


df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')



In [49]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'Classe', 'SKU', 'Descrição', 'Subcategoria', 'Lançamento',
       'Desativação', 'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 2025

In [50]:
df_final['PRODUTO SIMILAR']

0        52004
14       52004
28       52004
42       52004
56       52004
         ...  
19192    87771
19193    87771
19194    87771
19195    87771
19196    87771
Name: PRODUTO SIMILAR, Length: 2291, dtype: Int64

In [51]:
df_venda_diaria

PDV     SKU                                 DESCRICAO  \
0        12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1        20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2        20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3         5699  47.950                          ZAAD EDP 95ml V6   
4        20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   
...        ...     ...                                       ...   
1663315  20996  83.039                 QUASAR DES COL RUSH 100ml   
1663316  20970  52.025           BOTI BABY SAB LIQ GLIC V2 400ml   
1663317  20996  93.069  LA PIEL D/COL SPR CP PER AMBR DOUR 200ml   
1663318  13427  51.279         MAKE B BAS LIQ C/ GLYC TX 140 30g   
1663319  21278  52.014    CJ FLAC OUI EDP ICONIQUE INTENSE 3x1ml   

         Vendas Ciclo Lançamento    Ciclo  
0                             11  C202307  
1                              1  C202405  
2                              5  C202409  
3                             12  C202406  
4                              2  C202416  
...                          ...      ...  
1663315                        1  C202415  
1663316                        6  C202511  
1663317                       10  C202414  
1663318                        1  C202309  
1663319                        2  C202511  

[1663320 rows x 5 columns]

In [52]:
df_venda_diaria['SKU'] = df_venda_diaria['SKU'].astype('str')

df_venda_diaria['SKU'] = df_venda_diaria['SKU'].str.replace('.','')

df_venda_diaria.head()

PDV    SKU                                 DESCRICAO  \
0  12522  51944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47950                          ZAAD EDP 95ml V6   
4  20993  50297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [53]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('str')

In [54]:
df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0                59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
14               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
28               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
42               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
56               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
14           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
28           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
42           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
56           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   

   FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ...  Ciclo_x  \
0   Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...  C202515   
14  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...  C202515   
28  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...  C202515   
42  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...  C202515   
56  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...  C202515   

   INICIO CICLO_x FIM CICLO_x DURAÇÃO_x  match_y  dias_ate_inicio  Ciclo_y  \
0      2025-10-13  2025-11-02        21        1               59  C202315   
14     2025-10-13  2025-11-02        21        1               59  C202315   
28     2025-10-13  2025-11-02        21        1               59  C202315   
42     2025-10-13  2025-11-02        21        1               59  C202315   
56     2025-10-13  2025-11-02        21        1               59  C202315   

   INICIO CICLO_y FIM CICLO_y DURAÇÃO_y  
0      2023-10-16  2023-10-29      14.0  
14     2023-10-16  2023-10-29      14.0  
28     2023-10-16  2023-10-29      14.0  
42     2023-10-16  2023-10-29      14.0  
56     2023-10-16  2023-10-29      14.0  

[5 rows x 79 columns]

In [55]:
df_final = pd.merge(left=df_final, right = df_venda_diaria[['PDV','SKU','Ciclo','Vendas Ciclo Lançamento']], right_on=['Ciclo','SKU','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [56]:
df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   

  PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
1           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
2           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
3           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
4           52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   

  FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ... DURAÇÃO_x  \
0  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
1  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
2  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
3  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
4  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   

  match_y dias_ate_inicio  Ciclo_y  INICIO CICLO_y  FIM CICLO_y DURAÇÃO_y  \
0       1              59  C202315      2023-10-16   2023-10-29      14.0   
1       1              59  C202315      2023-10-16   2023-10-29      14.0   
2       1              59  C202315      2023-10-16   2023-10-29      14.0   
3       1              59  C202315      2023-10-16   2023-10-29      14.0   
4       1              59  C202315      2023-10-16   2023-10-29      14.0   

   SKU_y    Ciclo Vendas Ciclo Lançamento  
0  52004  C202315                      22  
1  52004  C202315                      36  
2  52004  C202315                       9  
3  52004  C202315                       5  
4  52004  C202315                      28  

[5 rows x 82 columns]

In [57]:
df_final.to_excel(r'C:\Users\joao.herculano\Documents\teste.xlsx',index=False)

In [58]:
df_final = df_final[df_final['PRODUTO LANÇAMENTO'].notna()]
df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)


In [59]:
df_final['PDV'].value_counts().min()

np.int64(29)

In [60]:
df_final.columns[29:46]

Index(['Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509'],
      dtype='object')

In [61]:
df_jacobina = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\REGIÃO JACOBINA\draft unificado.xlsx")

In [62]:
df_jacobina = df_jacobina[['PDV', 'SKU','202408', '202409',
       '202410', '202411', '202412', '202413', '202414', '202415', '202416',
       '202417', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507']]

In [63]:
ciclos = [
    '202408', '202409', '202410', '202411', '202412', '202413',
    '202414', '202415', '202416', '202417', '202501', '202502',
    '202503', '202504', '202505', '202506', '202507']

df_jacobina[ciclos] = df_jacobina[ciclos].fillna(0)

In [64]:
df_jacobina.head()

PDV    SKU  202408  202409  202410  202411  202412  202413  202414  \
0  24269  49014       1       0       5       1       1       1       2   
1  24268  49014       1       0       4       4       2       5       1   
2  24269  49016      36       3       1       1       1       0      14   
3  24268  49016      12       3       1       2       2       2       0   
4  24269  48141      32       2       3      95       3       2      41   

   202415  202416  202417  202501  202502  202503  202504  202505  202506  \
0       2       1       1       3       0       4       0       2       1   
1       3       4       4       3       0       2       4       2       0   
2       2       2       1       1      19       1       2       2      10   
3       0       3      11       4       3       0       4       2       1   
4       3       3       1       1       1       0      67       4      10   

   202507  
0       0  
1       1  
2       0  
3       0  
4       2

In [65]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
1            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
2            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
3            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
4            52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   

  FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ... DURAÇÃO_x  \
0  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
1  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
2  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
3  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   
4  Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...        21   

  match_y dias_ate_inicio  Ciclo_y  INICIO CICLO_y  FIM CICLO_y DURAÇÃO_y  \
0       1              59  C202315      2023-10-16   2023-10-29      14.0   
1       1              59  C202315      2023-10-16   2023-10-29      14.0   
2       1              59  C202315      2023-10-16   2023-10-29      14.0   
3       1              59  C202315      2023-10-16   2023-10-29      14.0   
4       1              59  C202315      2023-10-16   2023-10-29      14.0   

   SKU_y    Ciclo Vendas Ciclo Lançamento  
0  52004  C202315                      22  
1  52004  C202315                      36  
2  52004  C202315                       9  
3  52004  C202315                       5  
4  52004  C202315                      28  

[5 rows x 82 columns]

In [66]:
df_final = pd.merge(left=df_final,right=df_jacobina,left_on=['PRODUTO SIMILAR','PDV'],right_on=['SKU','PDV'],how='left')

In [67]:
# Gera pares de colunas: coluna estática ↔ coluna de histórico
pares_validos = [
    (ciclo, f'Histórico de Vendas do Ciclo {ciclo}')
    for ciclo in ciclos
    if ciclo in df_final.columns and f'Histórico de Vendas do Ciclo {ciclo}' in df_final.columns
]

# Separa os nomes das colunas
colunas_estaticas = [c[0] for c in pares_validos]
colunas_historico = [c[1] for c in pares_validos]

# Aplica a regra: se valor na coluna estática for maior, sobrescreve no histórico
for col_estatica, col_hist in zip(colunas_estaticas, colunas_historico):
    df_final[col_hist] = df_final[col_estatica].where(
        df_final[col_estatica] > df_final[col_hist],
        df_final[col_hist]
    )


In [68]:
df_final

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4                  59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
...                  ...                                                ...   
2286               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2287               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2288               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2289               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   
2290               87771              MAKE B BLUSH COMP BERRY MINI PRM 1,5g   

      PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
1               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
2               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
3               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
4               52004  NSPA LOC RAD DES HID CPO AMEI DOUR 400ml       C202315   
...               ...                                       ...           ...   
2286            87771                                         0             0   
2287            87771                                         0             0   
2288            87771                                         0             0   
2289            87771                                         0             0   
2290            87771                                         0             0   

     FOCO  IAF            CATEGORIA       MARCA   % CONSUMIDOR  ... 202415  \
0     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...    NaN   
1     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...    NaN   
2     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...    NaN   
3     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...    NaN   
4     Sim  Sim  CUIDADOS COM A PELE  NATIVA SPA  31,07 | 39,52  ...    NaN   
...   ...  ...                  ...         ...            ...  ...    ...   
2286  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...    NaN   
2287  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...    NaN   
2288  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...    NaN   
2289  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...    NaN   
2290  Não  Não      SUPORTE À VENDA     MAKE B.              -  ...    NaN   

     202416 202417 202501  202502  202503 202504 202505 202506 202507  
0       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
1       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
3       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
4       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
...     ...    ...    ...     ...     ...    ...    ...    ...    ...  
2286    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2287    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2288    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2289    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2290    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  

[2291 rows x 100 columns]

In [69]:
df_final = df_final.fillna(0)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_101180\260461722.py:1: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_final = df_final.fillna(0)


In [70]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[29:46]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

CRESCIMENTO = 0.2 if CRESCIMENTO < 0.2 else CRESCIMENTO

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


np.float64(0.2267)

In [71]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [72]:
df_final.columns[40:47]

Index(['Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [73]:
VENDA_SIMILAR_6_MESES= df_final.columns[40:47]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final['Pico Vendas Similar Ultimos 6 ciclos'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].median(axis=1, skipna=True)




In [74]:
df_final[colunas_mensais].median(axis=1, skipna=True)


0       2.0
1       2.0
2       0.0
3       0.0
4       1.0
       ... 
2286    0.0
2287    0.0
2288    0.0
2289    0.0
2290    0.0
Length: 2291, dtype: float64

In [75]:
medi = df_final.groupby(['CANAL','UF'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})
medi

CANAL   UF  med_por_canal
0     CD   AL          618.0
1    HIB   AL           50.0
2    HIB   BA           96.0
3    HIB  BA3            0.0
4    HIB   SE           42.0
5     LJ   AL           87.0
6     LJ   BA           25.0
7     LJ  BA3           19.0
8     LJ   SE           20.0
9     VD   AL          202.0
10    VD   BA          205.0
11    VD  BA3           47.0
12    VD   SE          164.0

In [76]:
#df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF'],how='inner')


In [77]:
df_final['TIPO DE PRODUTO']

0       LANÇAMENTO
1       LANÇAMENTO
2       LANÇAMENTO
3       LANÇAMENTO
4       LANÇAMENTO
           ...    
2286      PROMOÇÃO
2287      PROMOÇÃO
2288      PROMOÇÃO
2289      PROMOÇÃO
2290      PROMOÇÃO
Name: TIPO DE PRODUTO, Length: 2291, dtype: object

In [78]:
df_venda_diaria.head()

PDV    SKU                                 DESCRICAO  \
0  12522  51944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47950                          ZAAD EDP 95ml V6   
4  20993  50297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [79]:
df_dourado = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\DADOS DOURADO\VENDA\compilado de vendas.xlsx")

df_dourado['Data de venda'] = pd.to_datetime(df_dourado['Data de venda'], dayfirst=True)

df_dourado['de para pdv'] = df_dourado['de para pdv'].astype(str)

df_dourado['de para pdv'] = df_dourado['de para pdv'].str.replace(r'\.0$', '', regex=True)

# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'SKU', 'Ciclo'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_dourado['Quantidade Acumulada dourado'] = (
    df_dourado
    .groupby(['de para pdv', 'sku'])['Quantidade Vendida']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_dourado = pd.merge(left=df_dourado,right=calendario[['Date','Ciclo']],left_on='Data de venda',right_on='Date',how='inner')



df_dourado_agrupado = df_dourado.groupby(['de para pdv','sku','Ciclo'])['Quantidade Acumulada dourado'].max().reset_index()

df_dourado_agrupado = df_dourado_agrupado.rename(columns={'Ciclo':'Ciclo dourado'})



In [80]:
df_final['PDV'] = df_final['PDV'].astype(str)
df_final['PDV'].head()

0    12522
1    12817
2    12818
3    12820
4    12823
Name: PDV, dtype: object

In [81]:
df_final = pd.merge(left=df_final, right = df_dourado_agrupado, right_on=['Ciclo dourado','sku','de para pdv'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada dourado'] = df_final['Quantidade Acumulada dourado'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada dourado'] > 0, df_final['Quantidade Acumulada dourado'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada dourado')


df_final = df_final.drop(columns='Ciclo dourado')

In [82]:
df_depara_vdc = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\Filiais - Vitoria da Conquista 4.xlsx")

df_depara_vdc.head()

CP VIVA BEM  Protheus  PDVDEPARA.Practico        Canal  \
0         3559   70101.0             23713.0  MATRIZ - LJ   
1         7292   70103.0             23712.0         LOJA   
2         8708   70102.0             23711.0           VD   
3         8931       NaN             23710.0          NaN   
4        11191   70108.0             23709.0         LOJA   

                                            Endereço                CNPJ  \
0  Rua Zeferino Correia, nº 17, Centro, CEP 45.00...  14.378.160/0001-83   
1  Al. Rio Branco, nº 373, Centro, Cândido Sales ...  14.378.160/0006-98   
2  Al. Lima Guerra, nº 04, Centro, Vitória da Con...  14.378.160/0005-07   
3  Avenida Rosa Cruz, nº 80, Hiper B Preço Loja B...  14.378.160/0008-50   
4  Av. Juracy Magalhães, nº 3340, Shopping Conqui...  14.378.160/0009-30   

         CNPJ Locação  
0  14.378.160/0001-83  
1  14.378.160/0006-98  
2  14.378.160/0001-83  
3  14.378.160/0008-50  
4  14.378.160/0001-83

In [83]:
df_vdc = pd.read_parquet(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\VENDAS VITORIA DA CONQUISTA\concatenado.parquet")

df_vdc['PDV'] = df_vdc['Quebra'].str.split(" -").str[0]

df_vdc['PDV'] = df_vdc['PDV'].astype('int64')

df_vdc = df_vdc.rename(columns={'Quebra2':'DATA VENDA'})

df_vdc['DATA VENDA'] = pd.to_datetime(df_vdc['DATA VENDA'], format='%d/%m/%Y')

In [84]:
df_vdc = pd.merge(df_vdc,df_depara_vdc[['CP VIVA BEM','PDVDEPARA.Practico']],left_on='PDV',right_on='CP VIVA BEM',how='inner')

df_vdc['Quantidade'] = df_vdc['Quantidade'].str.replace(r',000$','',regex=True)

df_vdc['Quantidade'] = df_vdc['Quantidade'].astype('Int64') 

In [85]:




# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
#df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'SKU', 'Ciclo'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_vdc['Quantidade Acumulada vdc'] = (
    df_vdc
    .groupby(['PDVDEPARA.Practico', 'Código'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

In [86]:
df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')

df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})


df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str).str.replace(r'\.0$', '', regex=True)
df_vdc_agrupado.head()



PDVDEPARA.Practico  Código Ciclo vdc  Quantidade Acumulada vdc
0              23701    1004   C202203                     139.0
1              23701    1004   C202204                     161.0
2              23701    1004   C202205                     162.0
3              23701    1004   C202206                       9.0
4              23701    1004   C202207                      15.0

In [87]:
df_vdc_agrupado = df_vdc_agrupado.astype(str)

df_vdc_agrupado = df_vdc_agrupado.replace()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_101180\3455958411.py:3: FutureWarning: DataFrame.replace without 'value' and with non-dict-like 'to_replace' is deprecated and will raise in a future version. Explicitly specify the new values instead.
  df_vdc_agrupado = df_vdc_agrupado.replace()


In [88]:
#df_vdc.to_excel(r"C:\Users\joao.herculano\Documents\df_vdc.xlsx",index=False)

In [89]:
df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str)

df_vdc_agrupado['PDVDEPARA.Practico'].head()

0    23701
1    23701
2    23701
3    23701
4    23701
Name: PDVDEPARA.Practico, dtype: object

In [90]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

In [91]:
df_vdc_agrupado['Código'] = df_vdc_agrupado['Código'].astype('Int64')

In [92]:
df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = pd.to_numeric(
    df_final['Quantidade Acumulada vdc'],
    errors='coerce'  # valores inválidos viram NaN
).fillna(0).astype('Int64')


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc'] > 0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')



In [93]:

# Cálculo do crescimento
crescimento_final = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']
crescimento_final = crescimento_final.clip(lower=0.2, upper=0.8)  # limita entre 0 e 0.8
df_final['CRESCIMENTO_FINAL'] = crescimento_final

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_FINAL'].isna(),df_final['CRESCIMENTO_GERAL'],df_final['CRESCIMENTO_FINAL'])

df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_FINAL'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)

# Corrige mediana do histórico onde for zero
df_final['MEDIANA DO HISTÓRICO'] = np.where(
    df_final['MEDIANA DO HISTÓRICO'] == 0,
    0,
    df_final['MEDIANA DO HISTÓRICO']
)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)



# Cálculo do PV GINSENG
pv_crescimento = (df_final['CRESCIMENTO_FINAL']+1) * df_final['Vendas Ciclo Lançamento']
pv_mediana = (df_final['CRESCIMENTO_FINAL'] + 1) * df_final['MEDIANA DO HISTÓRICO']

df_final['PV GINSENG'] = np.where(
    pv_crescimento < df_final['MEDIANA DO HISTÓRICO'],
    pv_mediana.round(0),
    pv_crescimento.round(0)
)

# Se PV GINSENG for NA, substitui pela média por canal
df_final['PV GINSENG'] = df_final['PV GINSENG'].fillna(0)

df_final['PV GINSENG'] = df_final['PV GINSENG'].round(0).astype(int)

df_final.shape


(2291, 108)

In [94]:
df_final.to_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\validação.xlsx",index=False)

In [95]:
print(df_final.columns[30:43])

df_final.drop(columns=df_final.columns[30:43],inplace=True)

Index(['Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506'],
      dtype='object')


In [96]:
df_final.columns[29:34]

Index(['Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [97]:
df_final = df_final.rename(columns={df_final.columns[30]: "C-4", df_final.columns[31]: "C-3",df_final.columns[32]: "C-2",df_final.columns[29]: "C-1",df_final.columns[33]:'VENDAS CICLO ATUAL'})


In [98]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='HISTÓRICO DE VENDAS DO CICLO').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'CLASSE', 'SKU_X', 'DESCRIÇÃO', 'SUBCATEGORIA', 'LANÇAMENTO',
       'DESATIVAÇÃO', 'C-1', 'C-4', 'C-3', 'C-2', 'VENDAS CICLO ATUAL',
       'DIAS SEM VENDA', 'PROJEÇÃO PRÓXIMO CICLO',
       'PROJEÇÃO PRÓXIMO CICLO + 1', 'PROMOÇÃO PRÓXIMO CICLO',
       'PROMOÇÃO PRÓXIMO CICLO + 1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'COMPRA INTELIGENTE SEMANAL/SUGESTÃO DE COMPRA',
       'COMPRA INTELIGENTE PRÓXIMO CICLO',
       'COMPRA INTELIGENTE PRÓXIMO CICLO + 1', 'ITEM DESATIVADO',
       'DATA PREVISTA REGULARIZAÇÃO', 'CARTEIRA BLOQUEADA PARA NOVOS PEDIDOS',
       'PLANOGRAMA', 'QUANTIDADE P

In [99]:
df_final = df_final.rename(columns={'MARCA_X':'MARCA'})

In [100]:
df_final.shape

(2291, 94)

In [101]:
df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']] = df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']].fillna(0)

In [102]:
df_final = df_final.loc[:, ~df_final.columns.duplicated()]

colunas_desejadas = [
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    '% CONSUMIDOR',
    'MECANICA CONSUMIDOR',
    '% REVENDEDOR',
    'MECANICA REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'
]

df_final = df_final.reindex(columns=colunas_desejadas)

colunas_filtradas = [col for col in colunas_desejadas if col in df_final.columns]
df_final = df_final[colunas_filtradas]


In [103]:
'''df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'])
'''

"df_final = df_final.reindex(columns=[\n    'SUPERVISOR',\n    'ANALISTA',\n    'CANAL',\n    'UF',\n    'PDV',\n    'DESCRIÇÃO PDV',\n    'PRODUTO LANÇAMENTO',\n    'DESCRIÇÃO DO LANÇAMENTO',\n    'MARCA',\n    'CATEGORIA',\n    'MECANICA CONSUMIDOR',\n    '% CONSUMIDOR',\n    'MECANICA REVENDEDOR',\n    '% REVENDEDOR',\n    'TIPO DE PRODUTO',\n    'IAF',\n    'FOCO',\n    'PRODUTO SIMILAR',\n    'DESCRIÇÃO SIMILAR',\n    'CICLO SIMILAR',\n    'VENDAS CICLO LANÇAMENTO',\n    'C-4',\n    'C-3',\n    'C-2',\n    'C-1',\n    'VENDAS CICLO ATUAL',\n    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',\n    'PV GINSENG'])\n"

In [104]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [105]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype(str)

df_pdv_origi['PDV'].head()

df_pdv_origi = df_pdv_origi.rename(columns={'UF':'UF_CERTO'})

In [106]:
df_final= pd.merge(df_final,df_pdv_origi[['UF_CERTO','PDV']],on='PDV',how='inner')

In [107]:
df_final.columns

Index(['SUPERVISOR', 'ANALISTA', 'CANAL', 'UF', 'PDV', 'DESCRIÇÃO PDV',
       'PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'MARCA', 'CATEGORIA',
       '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'IAF', 'FOCO',
       'PRODUTO SIMILAR', 'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR',
       'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
       'SUGESTÃO COMERCIAL', 'UF_CERTO'],
      dtype='object')

In [108]:
df_final['UF']= df_final['UF_CERTO']

df_final = df_final.drop(columns=['UF_CERTO'])

df_final.head()

SUPERVISOR   ANALISTA CANAL  UF    PDV    DESCRIÇÃO PDV  \
0  Efigênia Herculano       LUAN    LJ  AL  12522  MACEIO SHOP EXP   
1      Maxwell Vieira  JEFFERSON    LJ  AL  12817   SHOPPING PATIO   
2      Maxwell Vieira      PEDRO    LJ  AL  12818      GB SERRARIA   
3      Maxwell Vieira   THAYLLAN    LJ  AL  12820         ATACADÃO   
4  Efigênia Herculano   MARCYARA    LJ  AL  12823      PONTA VERDE   

   PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
1               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
2               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
3               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   
4               59823  NATIVA SPA ORQUÍDEA LUMIÈRE CREME DESODORANTE ...   

        MARCA            CATEGORIA  ...  C-4  C-3  C-2  C-1  \
0  NATIVA SPA  CUIDADOS COM A PELE  ...  2.0  3.0  0.0  2.0   
1  NATIVA SPA  CUIDADOS COM A PELE  ...  3.0  0.0  0.0  3.0   
2  NATIVA SPA  CUIDADOS COM A PELE  ...  4.0  2.0  0.0  1.0   
3  NATIVA SPA  CUIDADOS COM A PELE  ...  0.0  2.0  0.0  1.0   
4  NATIVA SPA  CUIDADOS COM A PELE  ...  4.0  0.0  1.0  5.0   

  VENDAS CICLO ATUAL PICO VENDAS SIMILAR ULTIMOS 6 CICLOS PV GINSENG  \
0                0.0                                  3.0         27   
1                0.0                                  5.0         43   
2                4.0                                  4.0         11   
3                2.0                                  3.0          6   
4                5.0                                  7.0         34   

   SUGESTÃO METASELLIN SUGESTÃO ABASTECIMENTO SUGESTÃO COMERCIAL  
0                                                                 
1                                                                 
2                                                                 
3                                                                 
4                                                                 

[5 rows x 31 columns]

In [110]:
df_final.to_excel(f'C:/Users/joao.herculano/Documents/Lançamento{hoje}{ciclo_lanc}.xlsx',index=False)